(objective)=
# objective
An object to hold the information of the objective function after optimization. These objects are automatically created by SHOP, one objective object per scenario is created with the name 'scen_<number>'. In addition, the average objective weighted by the scenario probablities is created in every SHOP run. For a regular deterministic SHOP run, the average_objective and scen_1 objective will be identical.

|   |   |
|---|---|
|Input connections||
|Output connections||
|License|SHOP_OPEN|
|Release version|13.0.0.a|

```{contents}
:local:
:depth: 1
```

## Introduction

The objective function in an optimization model is the driving force of the model that evaluates how optimal a decision is. The objective function in SHOP is formulated to minimize the negative net profit, which is equivalent to maximizing the net profit. This convention means that a negative objective function is normal, while a positive objective function is concerning as the system is operated at a loss. The objective object in SHOP is automatically created by SHOP and only holds output attributes. The total objective function value in SHOP is saved to the objective object in the [grand_total](objective:grand_total) attribute, and it is the sum of several different parts which are explained in the following sub-sections. All parts of the objective function are measured in currency (NOK, €, etc.), and are shown as total sums over all time steps etc. in the optimization. 

## Financial income and costs

The most straightforward component of the objective function is direct financial incomes and costs. The most common financial income in SHOP is due to selling energy in the day-ahead [](market), which is saved to the [market_sale_buy](objective:market_sale_buy) attribute. This is the net sale to the market summed up for the entire optimization horizon, and a negative value indicates a net income in the market and a positive value indicates a net cost of trading in the market. The [reserve_sale_buy](objective:reserve_sale_buy) attribute holds the same information for trade in reserve capacity markets. The [load_value](objective:load_value) and [reserve_oblig_value](objective:reserve_oblig_value) shows the value of covering the load in energy and reserve markets, respectively. The [load_price](market:load_price) attribute on the market object can be used to specify the price for valuating the load, otherwise the [sale_price](market:sale_price) is used to valuate reserve market obligations and the average of the sale and [buy_price](market:buy_price) for valuating energy market loads. If financial [contracts](contract) are used, the [contract_value](objective:contract_value) attribute shows the total trade for all contracts and again a negative number indicates an overall net income. 

The start and stop costs of all units in the system is saved to the [startup_costs](objective:startup_costs) attribute, and other power generation costs such as [thermal_cost](objective:thermal_cost), [wind_curtailment_cost](objective:wind_curtailment_cost), and [solar_curtailment_cost](objective:solar_curtailment_cost) are also saved to the objective function. 

There are several other attributes ending in '_cost', but not all of these represent a concrete financial cost. Since everything must be converted to a cost in currency to be part of the objective function, model technical costs used to dissuade certain behaviour are also found in the objective function. An example of this is [gate_ramping_cost](objective:gate_ramping_cost) which is a small cost applied to changes in the flow in a [](gate) from time step to time step, which is used to smooth out the optimized flow in the gates.

## Future expected income

The largest part of the grand_total objective function value in SHOP is usually the future expected income from saving water in the [reservoirs](reservoir) for future use. There are several [water value descriptions](water-value-descriptions) in SHOP that can be used to formulate how much the reservoir contents of each reservoir in the system is worth at the end of the optimization horizon. The future expected cost of the system is found in the [rsv_end_value](objective:rsv_end_value) attribute, which is calculated based on the water value description used. The rsv_end_value should be a negative number, otherwise it indicates that there is a future net cost of operating the system. This can happen if penalties have influenced the cuts created in the long-/medium-term model that created the water value function. The [rsv_end_value_relative](objective:rsv_end_value_relative) attribute shows an approximation of the change in the value of the water from the beginning to the end of the optimization, which is calculated by evaluating the reservoir end value function on the start volume of all reservoirs. Note that this value is not part of the objective function in SHOP, but is still saved to the objective object. The [vow_in_transit](objective:vow_in_transit) attribute shows the end value of the water in transition at the end of the optimization period, which could happen when there are time delays in the waterways of the system.

## Penalties

Most attributes on the objective object in SHOP is related to various incurred penalties. A penalty is incurred in SHOP when a constraint is 'knowingly' violated by the optimization. There are many potentially conflicting constraints that can be applied to SHOP, and having the option to take a (high) penalty and not fulfil a constraint is often preferable to ending up with an infeasible (unsolvable) model. The [sum_penalties](objective:sum_penalties) attribute holds the sum of all penalties that have been incurred, and will always be greater or equal to zero. The penalties are further categorized as [minor](objective:minor_penalties) and [major](objective:major_penalties), and the sum of these add up to the sum_penalties attribute. Whether breaking a certain constraint should be considered a 'minor' or 'major' incident is subjective and highly case dependent, so the categorization is only a guideline. 

## Solver status

The [solver_status](objective:solver_status) from the third party solver [CPLEX](https://www.ibm.com/products/ilog-cplex-optimization-studio) used in SHOP is saved on the objective object. The status is saved as a string, and the most encountered return values are listed below:

|Solver status|Severity|Rarity|Comment|
|-|-|-|-|
|Optimal solution is available|0|Common|The model has been solved to optimality|
|Optimal integer solution found|0|Rare|The MILP model has been solved to optimality|
|Optimal whithin tolerances|0|Common|The MILP model has been solved to within the numerical tolerances defined by the [MIP gaps](set_mipgap)|
|Time limit exceeded, integer solution exists|1|Common|The MILP model has not been solved to within the numerical tolerances in the given [time limit](global_settings:timelimit), but a solution exists|
|Optimal solution is available, but with infeasibilities after unscaling|1|Rare|The model was solved to optimality, but numerical problems exist|
|Solution is available, but not proved optimal, due to numeric difficulties during optimization|1|Very rare|The model was not proven to be optimal due to numerical problems|
|Model has been proved infeasible|2|Rare|The model is unsolvable due to conflicting constraints|
|Integer infeasible|2|Rare|The MILP model is unsolvable due to conflicting constraints|
|Integer infeasible or unbounded|2|Rare|The MILP model is unsolvable due to conflicting constraints or an infinite objective function|
|Model has an Unbounded ray|2|Very rare|The MILP model is unsolvable due to conflicting constraints or an infinite objective function|
|Time limit exceeded, no integer solution exists|2|Rare|No solutions to the MILP model was found within the given time limit|
|Calculation not completed, exceeding time limit|2|Very rare|The model was not solved within the given time limit|

A severity rating of zero in the table above means that everything has gone well in the optimization. This does not mean that there are no penalties or other problems, but the problems are not caused by difficulties in solving the model itself. A severity of 1 means that the solution might be sub-optimal or experience numerical problems, but is usually not a cause for concern if only present in a few iterations. A severity of 2 means that the model has not been solved, and the SHOP run has failed. Increasing the time limit might be necessary for large (MILP) problems, but infeasible or unbounded models have severe underlying issues. Hints to which constraints and variables constitute the infeasibility are printed to the SHOP log file.

The solver_status is an output attribute and therefore updated after each iteration in SHOP. This means that a problematic solver status in one iteration is lost unless the user checks after every SHOP iteration.





## Attributes

In [1]:
from IPython.core.display import HTML
HTML("""<table id="objective-table" class="display compact"></table>
<script>
enableDataTable(
  "#objective-table",
  "/_static/data/objective-attribute-table.json"
);
</script>
""")

(objective:solver_status)=
### solver_status
Description of the latest status from the solver (xUnit: NO_UNIT, yUnit: NO_UNIT)


(objective:times_of_wrong_pq_uploading)=
### times_of_wrong_pq_uploading
How many times the unit PQ segments are wrongly uploaded, i.e. the latter segments are fulfilled first. (xUnit: NO_UNIT, yUnit: NO_UNIT)


(objective:grand_total)=
### grand_total
Objective function equal to the sum of total and sum_penalties (xUnit: NOK, yUnit: NOK)


(objective:sim_grand_total)=
### sim_grand_total
Simulated objective function equal to the sum of total and sum_penalties (xUnit: NOK, yUnit: NOK)


(objective:total)=
### total
Objective function equal to the sum of rsv_end_value, vow_in_transit, market_sale_buy, load_value, reserve_sale_buy, reserve_oblig_value, contract_value, startup_costs, sum_feeding_fee, and sum_discharge_fee (xUnit: NOK, yUnit: NOK)


(objective:sum_penalties)=
### sum_penalties
Penalty cost equal to the sum of minor_penalties and major_penalties (xUnit: NOK, yUnit: NOK)


(objective:minor_penalties)=
### minor_penalties
Penalty cost equal to the sum of rsv_tactical_penalty, rsv_peak_volume_penalty, rsv_flood_volume_penalty, river_flow_penalty, river_peak_flow_penalty, river_gate_adjustment_penalty, gate_q_constr_penalty, gate_peak_flow_penalty, gate_discharge_cost, bypass_cost, gate_spill_cost, gate_slack_cost, gate_ramping_cost, creek_spill_cost, junction_slack_cost, plant_p_constr_penalty, plant_q_constr_penalty, plant_schedule_penalty, gen_schedule_penalty, pump_schedule_penalty, reserve_violation_penalty, reserve_slack_cost, reserve_schedule_penalty, wind_curtailment_cost, solar_curtailment_cost, plant_reserve_discharge_penalty, plant_sum_reserve_penalty, reserve_activation_penalty, reserve_tactical_activation_penalty, and plant_reserve_strategy_penalty (xUnit: NOK, yUnit: NOK)


(objective:major_penalties)=
### major_penalties
Penalty cost equal to the sum of rsv_penalty, rsv_end_penalty, rsv_hard_limit_penalty, rsv_over_limit_penalty, river_min_flow_penalty, river_max_flow_penalty, river_flow_schedule_penalty, load_penalty, group_time_period_penalty, group_time_step_penalty, discharge_group_penalty, production_group_energy_penalty, production_group_power_penalty, and sum_ramping_penalty (xUnit: NOK, yUnit: NOK)


(objective:rsv_end_value)=
### rsv_end_value
Value of water remaining in the reservoirs at the end of the optimization period. If cut description is used, the delayed water on its way to reservoirs is included, while for other end value description this water is valuated in vow_in_transit. (xUnit: NOK, yUnit: NOK)


(objective:sim_rsv_end_value)=
### sim_rsv_end_value
Simulated value of water remaining in the reservoirs at the end of the simulation period. (xUnit: NOK, yUnit: NOK)


(objective:rsv_end_value_relative)=
### rsv_end_value_relative
Change in value of water in the reservoirs between the start and the end of the optimization period (xUnit: NOK, yUnit: NOK)


(objective:vow_in_transit)=
### vow_in_transit
Value of delayed water on its way to reservoirs at the end of the optimization period. If cut description is used the delayed water is valuated as part of the rsv_end_value instead. (xUnit: NOK, yUnit: NOK)


(objective:rsv_spill_vol_end_value)=
### rsv_spill_vol_end_value
End reservoir value lost due to volume over HRL in flood situations. Only appliccapble when running with constant water values. The extra water is evaluated according to the water value of the reservoir downstream of the spill gate. (xUnit: NOK, yUnit: NOK)


(objective:market_sale_buy)=
### market_sale_buy
The sum of the value of power bought from the market minus the value of power sold to the market for all time steps (xUnit: NOK, yUnit: NOK)


(objective:sim_market_sale_buy)=
### sim_market_sale_buy
The sum of the simulated value of power bought from the market minus the value of power sold to the market for all time steps (xUnit: NOK, yUnit: NOK)


(objective:load_value)=
### load_value
The load obligation value by multiplying the load with the load price. If the load price is not given, the sale price is used. (xUnit: NOK, yUnit: NOK)


(objective:reserve_sale_buy)=
### reserve_sale_buy
Reserve trade value (xUnit: NOK, yUnit: NOK)


(objective:reserve_oblig_value)=
### reserve_oblig_value
THe reserve obligation value by multiplying the reserve obligation with the reserve obligation price. If the reserve obligation price is not given, the reserve sale price is used. (xUnit: NOK, yUnit: NOK)


(objective:contract_value)=
### contract_value
Contract value (xUnit: NOK, yUnit: NOK)


(objective:startup_costs)=
### startup_costs
The sum of the startup and shutdown costs for all units and time steps. By default this includes costs whenever the commitment status of the unit changes regardless of whether MIP is active or not. (xUnit: NOK, yUnit: NOK)


(objective:sim_startup_costs)=
### sim_startup_costs
The sum of simulated startup and shutdown costs for all units and time steps. By default this includes costs whenever the commitment status of the unit changes regardless of whether MIP is active or not. (xUnit: NOK, yUnit: NOK)


(objective:sum_feeding_fee)=
### sum_feeding_fee
The sum of feed-in fee paid for all plants and time steps. (xUnit: NOK, yUnit: NOK)


(objective:sum_discharge_fee)=
### sum_discharge_fee
The sum of discharge fee paid for all plants and gates and time steps. (xUnit: NOK, yUnit: NOK)


(objective:thermal_cost)=
### thermal_cost
The sum of fuel cost for all thermal units and time steps. (xUnit: NOK, yUnit: NOK)


(objective:production_cost)=
### production_cost
The sum of production cost for all units that has production_cost due to turbine partial damage. (xUnit: NOK, yUnit: NOK)


(objective:reserve_allocation_cost)=
### reserve_allocation_cost
The total cost for allocating reserves on all units in the system. The allocation cost can be specified on each unit for each reserve type, see for instance the 'fcr_n_up_cost' on the generator and pump objects. (xUnit: NOK, yUnit: NOK)


(objective:incurred_droop_cost)=
### incurred_droop_cost
The total incurred cost for the optimized droop settings on all units in the system delivering FCR reserves (xUnit: NOK, yUnit: NOK)


(objective:rsv_tactical_penalty)=
### rsv_tactical_penalty
Resulting total penalty cost when the tactical maximum or minimum volume limits for the reservoirs are violated (xUnit: NOK, yUnit: NOK)


(objective:plant_p_constr_penalty)=
### plant_p_constr_penalty
Resulting total penalty cost when the time-dependent maximum or minimum production limits for the plants are violated (xUnit: NOK, yUnit: NOK)


(objective:plant_q_constr_penalty)=
### plant_q_constr_penalty
Resulting total penalty cost when the time-dependent maximum or minimum discharge limits for the plants are violated (xUnit: NOK, yUnit: NOK)


(objective:plant_schedule_penalty)=
### plant_schedule_penalty
Resulting total penalty cost when the plant schedules are violated (xUnit: NOK, yUnit: NOK)


(objective:plant_rsv_q_limit_penalty)=
### plant_rsv_q_limit_penalty
Resulting total penalty cost when the head dependent maximum discharge limits for the plants are violated. These limits are set by the max_q_limit_rsv_up and max_q_limit_rsv_down attributes on the plant object (xUnit: NOK, yUnit: NOK)


(objective:gen_schedule_penalty)=
### gen_schedule_penalty
Resulting total penalty cost when the generator schedules are violated (xUnit: NOK, yUnit: NOK)


(objective:pump_schedule_penalty)=
### pump_schedule_penalty
Resulting total penalty cost when the pump schedules are violated (xUnit: NOK, yUnit: NOK)


(objective:gate_q_constr_penalty)=
### gate_q_constr_penalty
Resulting total penalty cost when the time-dependent maximum or minimum discharge limits for the gates are violated (xUnit: NOK, yUnit: NOK)


(objective:gate_discharge_cost)=
### gate_discharge_cost
The sum of discharge costs for all gates and time steps (xUnit: NOK, yUnit: NOK)


(objective:bypass_cost)=
### bypass_cost
The sum of bypass discharge costs for all bypass gates and time steps (xUnit: NOK, yUnit: NOK)


(objective:gate_spill_cost)=
### gate_spill_cost
The sum of spill costs for all spill gates and time steps (xUnit: NOK, yUnit: NOK)


(objective:physical_spill_cost)=
### physical_spill_cost
The sum of gate spill costs for the part of the spill that represents physical spill, i.e. the spill occurs when the water exceeds max_vol of the reservoir. (xUnit: NOK, yUnit: NOK)


(objective:physical_spill_volume)=
### physical_spill_volume
The sum of spill volume for the part of the spill that represents physical spill, i.e. the spill occurs when the water exceeds max_vol of the reservoir. (xUnit: MM3, yUnit: MM3)


(objective:nonphysical_spill_cost)=
### nonphysical_spill_cost
The sum of gate spill costs for the part of the spill that represents non-physical spill, i.e. the spill occurs when the water does not reach max_vol of the reservoir. (xUnit: NOK, yUnit: NOK)


(objective:nonphysical_spill_volume)=
### nonphysical_spill_volume
The sum of spill volume for the part of the spill that represents non-physical spill, i.e. the spill occurs when the water does not reach max_vol of the reservoir. (xUnit: MM3, yUnit: MM3)


(objective:gate_slack_cost)=
### gate_slack_cost
The sum of costs for the use of slack variables for all deltameter gates and time steps (xUnit: NOK, yUnit: NOK)


(objective:gate_ramping_cost)=
### gate_ramping_cost
The sum of cost for all gates ramping up or down and time steps (xUnit: NOK, yUnit: NOK)


(objective:creek_spill_cost)=
### creek_spill_cost
The sum of spill costs for all creek spill gates and time steps (xUnit: NOK, yUnit: NOK)


(objective:creek_physical_spill_cost)=
### creek_physical_spill_cost
The sum of creek spill costs for the part of the spill that represents physical spill (xUnit: NOK, yUnit: NOK)


(objective:creek_nonphysical_spill_cost)=
### creek_nonphysical_spill_cost
The sum of creek spill costs for the part of the spill that represents non-physical spill (xUnit: NOK, yUnit: NOK)


(objective:junction_slack_cost)=
### junction_slack_cost
The sum of cost for the use of slack variables for all junctions and time steps (xUnit: NOK, yUnit: NOK)


(objective:reserve_violation_penalty)=
### reserve_violation_penalty
Resulting total penalty cost when the reserve deliveries deviate below the reserve obligations (xUnit: NOK, yUnit: NOK)


(objective:reserve_slack_cost)=
### reserve_slack_cost
Resulting total slack cost when the reserve deliveries deviate above the reserve obligations (xUnit: NOK, yUnit: NOK)


(objective:reserve_schedule_penalty)=
### reserve_schedule_penalty
Resulting total penalty cost when the reserve schedules are violated (xUnit: NOK, yUnit: NOK)


(objective:rsv_peak_volume_penalty)=
### rsv_peak_volume_penalty
Resulting total penalty cost for peak reservoir volumes penalized by the peak_volume_cost_curve on each reservoir (xUnit: NOK, yUnit: NOK)


(objective:gate_peak_flow_penalty)=
### gate_peak_flow_penalty
Resulting total penalty cost for peak gate flows penalized by the peak_flow_cost_curve on each gate (xUnit: NOK, yUnit: NOK)


(objective:rsv_flood_volume_penalty)=
### rsv_flood_volume_penalty
Resulting total penalty cost for the reservoir volumes penalized by the flood_volume_cost_curve (xUnit: NOK, yUnit: NOK)


(objective:river_peak_flow_penalty)=
### river_peak_flow_penalty
Resulting total penalty cost for peak river flows penalized by the peak_flow_cost_curve on each river (xUnit: NOK, yUnit: NOK)


(objective:river_flow_penalty)=
### river_flow_penalty
Resulting total penalty cost for river flows penalized by the flow_cost_curve on each river (xUnit: NOK, yUnit: NOK)


(objective:river_gate_adjustment_penalty)=
### river_gate_adjustment_penalty
Resulting total penalty for adjusting the river gates according to the gate_adjustment_cost of each river (xUnit: NOK, yUnit: NOK)


(objective:plant_reserve_discharge_penalty)=
### plant_reserve_discharge_penalty
Resulting total penalty for violating the max and min discharge constraints on plants due to potential reserve activation (xUnit: NOK, yUnit: NOK)


(objective:solar_curtailment_cost)=
### solar_curtailment_cost
Resulting total cost of curtailing solar power (xUnit: NOK, yUnit: NOK)


(objective:wind_curtailment_cost)=
### wind_curtailment_cost
Resulting total cost of curtailing wind power (xUnit: NOK, yUnit: NOK)


(objective:plant_sum_reserve_penalty)=
### plant_sum_reserve_penalty
Resulting total penalty for violating the max upward and downward total reserve constraints on plants (xUnit: NOK, yUnit: NOK)


(objective:reserve_activation_penalty)=
### reserve_activation_penalty
Resulting total penalty for violating the reservoir volume constraints on reservoirs due to potential reserve activation (xUnit: NOK, yUnit: NOK)


(objective:reserve_tactical_activation_penalty)=
### reserve_tactical_activation_penalty
Resulting total penalty for violating the tactical reservoir volume constraints on reservoirs due to potential reserve activation (xUnit: NOK, yUnit: NOK)


(objective:plant_reserve_strategy_penalty)=
### plant_reserve_strategy_penalty
Resulting total penalty for violating the plant min and max reserve constraints that are based on the plant_max/min_reserve_strategy input (xUnit: NOK, yUnit: NOK)


(objective:rsv_penalty)=
### rsv_penalty
Resulting total penalty cost when the maximum or minimum volume limits for all reservoirs during the optimization period are violated (xUnit: NOK, yUnit: NOK)


(objective:rsv_hard_limit_penalty)=
### rsv_hard_limit_penalty
Resulting total penalty cost for breaking the hard min/max constraints on the reservoir volume or level (xUnit: NOK, yUnit: NOK)


(objective:rsv_over_limit_penalty)=
### rsv_over_limit_penalty
Resulting total penalty cost when the volume of reservoirs with an attached flood gate goes over the physical maximum volume limits (xUnit: NOK, yUnit: NOK)


(objective:sim_rsv_penalty)=
### sim_rsv_penalty
Simulated total penalty cost when the maximum or minimum volume limits for all reservoirs during the optimization period are violated (xUnit: NOK, yUnit: NOK)


(objective:rsv_end_penalty)=
### rsv_end_penalty
Resulting total penalty cost when the maximum or minimum volume limits for all reservoirs at the end of the optimization period are violated (xUnit: NOK, yUnit: NOK)


(objective:load_penalty)=
### load_penalty
Resulting total penalty cost when load obligations are violated (xUnit: NOK, yUnit: NOK)


(objective:group_time_period_penalty)=
### group_time_period_penalty
Resulting total penalty cost when period sum constraints on the old ascii multi-object format are violated. Sum over all constraints (xUnit: NOK, yUnit: NOK)


(objective:group_time_step_penalty)=
### group_time_step_penalty
Resulting total penalty cost when time-dependent constraints on the old ascii multi-object format are violated. Sum over all constraints and time steps (xUnit: NOK, yUnit: NOK)


(objective:sum_ramping_penalty)=
### sum_ramping_penalty
Resulting total penalty cost when ramping sum constraints on the old ascii format are violated. Sum over all constraints and time steps (xUnit: NOK, yUnit: NOK)


(objective:plant_ramping_penalty)=
### plant_ramping_penalty
Resulting total penalty cost when plnat production ramping constraints are violated. Sum over all plants and time steps (xUnit: NOK, yUnit: NOK)


(objective:rsv_ramping_penalty)=
### rsv_ramping_penalty
Resulting total penalty cost when reservoir storage ramping constraints are violated. Sum over all reservoirs and time steps (xUnit: NOK, yUnit: NOK)


(objective:gate_ramping_penalty)=
### gate_ramping_penalty
Resulting total penalty cost when discharge ramping constraints on gates are violated. Sum over all gates and time steps (xUnit: NOK, yUnit: NOK)


(objective:contract_ramping_penalty)=
### contract_ramping_penalty
Resulting total penalty cost when contract ramping constraints are violated. Sum over all contracts and time steps (xUnit: NOK, yUnit: NOK)


(objective:group_ramping_penalty)=
### group_ramping_penalty
Resulting total penalty cost when time-dependent group ramping constraints on the old ascii format are violated. Sum over all constraints and time steps (xUnit: NOK, yUnit: NOK)


(objective:discharge_group_penalty)=
### discharge_group_penalty
Resulting total penalty cost when the allowed deviations for discharge groups are violated. Sum for both upward and downward violation over all discharge groups and time steps (xUnit: NOK, yUnit: NOK)


(objective:discharge_group_ramping_penalty)=
### discharge_group_ramping_penalty
Resulting total penalty cost when the discharge ramping constraints for discharge groups are violated. Sum for both upward and downward violation over all discharge groups and time steps (xUnit: NOK, yUnit: NOK)


(objective:discharge_group_average_discharge_penalty)=
### discharge_group_average_discharge_penalty
Resulting total penalty cost when the average discharge constraints for discharge groups are violated. Sum for both upward and downward violation over all discharge groups and time steps (xUnit: NOK, yUnit: NOK)


(objective:production_group_energy_penalty)=
### production_group_energy_penalty
Resulting total penalty cost when the energy target production constraints on production groups are violated. Sum for both upward and downward violation over all production groups. (xUnit: NOK, yUnit: NOK)


(objective:production_group_power_penalty)=
### production_group_power_penalty
Resulting total penalty cost when the maximum or minimum power limit constraints on production groups are violated. Sum for both upward and downward violation over all production groups and time steps (xUnit: NOK, yUnit: NOK)


(objective:river_min_flow_penalty)=
### river_min_flow_penalty
Resulting total penalty for breaking the min_flow river constraints (xUnit: NOK, yUnit: NOK)


(objective:river_max_flow_penalty)=
### river_max_flow_penalty
Resulting total penalty for breaking the max_flow river constraints (xUnit: NOK, yUnit: NOK)


(objective:river_ramping_penalty)=
### river_ramping_penalty
Resulting total penalty cost when the discharge ramping constraints for rivers are violated. Sum for both upward and downward violation over all rivers and time steps (xUnit: NOK, yUnit: NOK)


(objective:river_gate_ramping_penalty)=
### river_gate_ramping_penalty
Resulting total penalty cost when the gate ramping constraints for rivers are violated. Sum for both upward and downward violation over all rivers and time steps (xUnit: NOK, yUnit: NOK)


(objective:river_flow_schedule_penalty)=
### river_flow_schedule_penalty
Resulting total penalty for breaking the flow_schedule river constraints (xUnit: NOK, yUnit: NOK)


(objective:level_rolling_ramping_penalty)=
### level_rolling_ramping_penalty
Resulting total penalty cost when the level rolling ramping constraints for reservoirs are violated. Sum for both upward and downward violation over all reservoirs and time steps (xUnit: NOK, yUnit: NOK)


(objective:level_period_ramping_penalty)=
### level_period_ramping_penalty
Resulting total penalty cost when the level period ramping constraints for reservoirs are violated. Sum for both upward and downward violation over all reservoirs and time steps (xUnit: NOK, yUnit: NOK)


(objective:discharge_rolling_ramping_penalty)=
### discharge_rolling_ramping_penalty
Resulting total penalty cost when the discharge rolling ramping constraints for plants are violated. Sum for both upward and downward violation over all plants and time steps (xUnit: NOK, yUnit: NOK)


(objective:discharge_period_ramping_penalty)=
### discharge_period_ramping_penalty
Resulting total penalty cost when the discharge period ramping constraints for plants are violated. Sum for both upward and downward violation over all plants and time steps (xUnit: NOK, yUnit: NOK)


(objective:rsv_nonseq_ramping_penalty)=
### rsv_nonseq_ramping_penalty
Resulting total penalty cost when the non-sequential reservoir ramping constraints are violated. Sum for both upward and downward violation over all reservoirs and time steps (xUnit: NOK, yUnit: NOK)


(objective:rsv_amplitude_ramping_penalty)=
### rsv_amplitude_ramping_penalty
Resulting total penalty cost when the amplitude reservoir ramping constraints are violated. Sum for both upward and downward violation over all reservoirs and time steps (xUnit: NOK, yUnit: NOK)


(objective:common_decision_penalty)=
### common_decision_penalty
Penalty cost for violating common decision period constraints in decomposed multi-scenario optimization problems (xUnit: NOK, yUnit: NOK)


(objective:bidding_penalty)=
### bidding_penalty
Penalty cost for violating constraints for increasing bid volume when price increases in decomposed multi-scenario optimization problems (xUnit: NOK, yUnit: NOK)


(objective:safe_mode_universal_penalty)=
### safe_mode_universal_penalty
Penalty cost for all violated constraints when universal penalty is switched on to investigate infeasibility (xUnit: NOK, yUnit: NOK)